# Imports

In [1]:
# defaults
import numpy as np
import pandas as pd

# regex
import re

# storing and loading models
import pickle

# to set types for functions
from typing import Tuple

# Plotting
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots


# gpu debug
import torch

# SBERT
from sentence_transformers import SentenceTransformer

# dimensionality reduction
from umap import UMAP

# clustering
from hdbscan import HDBSCAN

# topic finding
from sklearn.feature_extraction.text import TfidfVectorizer

# Loading model from pickle if possible, to avoid downloading it again
try:
    model = pickle.load(open('model.pkl', 'rb'))
    model_load = True

except:
    model = SentenceTransformer('all-mpnet-base-v2')
    pickle.dump(model, open('model.pkl', 'wb'))
    model_load = False

print(f"""
GPUs detected: {torch.cuda.device_count()}
Using GPU: {torch.cuda.is_available()}

Got model from pickle: {model_load}
""")

pd.set_option('display.max_colwidth', 200)


GPUs detected: 1
Using GPU: True

Got model from pickle: True



# Functions

## Feature Engineering and Cleaning

In [2]:
def string_cleaner(input: str) -> str:
    
    # turning lowercase
    input = input.lower()

    # removing punctuation and other non-alphanumeric characters
    input = re.sub(r'[^\w\s]', '', input)
    
    return input

## Plotting Helper Functions

In [3]:
def tfidf_most_relevant_word(input: list, num_words=5) -> list:

  most_relevant_words = []
  
  for corpus in input:
        
    vectorizer = TfidfVectorizer(stop_words='english')
    X = vectorizer.fit_transform(corpus)
    
    importance = np.argsort(np.asarray(X.sum(axis=0)).ravel())[::-1]
    tfidf_feature_names = np.array(vectorizer.get_feature_names_out()) # get_feature_names
    most_relevant_words.append(tfidf_feature_names[importance[:num_words]])

  return most_relevant_words



def topic_by_clusterId(result: pd.DataFrame) -> dict:
  df_group = result[["titles", "cluster_label"]].groupby("cluster_label").agg(list).reset_index()

  df_group["topics"] = tfidf_most_relevant_word(df_group["titles"])

  return dict(zip(df_group.cluster_label, df_group.topics))



def fig_show_save(fig: go.Figure, filename: str, show=True):
  filename = f"plots/{filename}.html"
  fig.write_html(filename)

  if show: 
    fig.show()

## Plotting

In [4]:
# when you actually cast the type here, then it works with how pandas casts types and you don't have to worry about copying seriers
def result_df_maker(embeddings: np.ndarray, cluster_labels: np.ndarray, titles: np.ndarray) -> pd.DataFrame:
  result = pd.DataFrame(embeddings, columns=['x', 'y'])

  result["titles"] = titles

  result["cluster_label"] = cluster_labels

  topic_dict = topic_by_clusterId(result)

  result["topics"] = result["cluster_label"].apply(lambda x: topic_dict[x])

  result["topics"] = result["topics"].apply(lambda x: " ".join(x))

  return result

def result_splitter(result: pd.DataFrame) -> Tuple[np.ndarray, np.ndarray]:
  clustered = result.loc[result.cluster_label != -1, :]
  outliers = result.loc[result.cluster_label == -1, :]
  return clustered, outliers

# the cavalry is not here, but it's fine! Why? I am here!
def result_tracer(clustered: pd.DataFrame, outliers: pd.DataFrame) -> Tuple[go.Scattergl, go.Scattergl]:
  trace_cluster = go.Scattergl(
    x=clustered.x, 
    y=clustered.y, 
    mode="markers", 
    name="Clustered",

    # styling markers
    marker=dict(
      size=2, 
      color=clustered.cluster_label,
      colorscale="Rainbow"
    ), 

    # setting hover text to the titles of the videos
    hovertemplate="<b>Topics:</b> %{customdata[0]} <br><b>Cluster Id:</b> %{customdata[1]}<extra></extra>", 
    customdata=np.column_stack([clustered.topics, clustered.cluster_label]),
  )

  trace_outlier = go.Scattergl(
    x=outliers.x,
    y=outliers.y,
    mode="markers",
    name="Outliers",

    marker=dict(
      size=1,
      color="grey"
    ),

    hovertemplate="Outlier<extra></extra>"
  )

  return trace_cluster, trace_outlier

def result_tracer_wrapper(uembs: np.ndarray, cluster_labels: np.ndarray, titles: np.ndarray) -> Tuple[go.Scattergl, go.Scattergl]:
  result = result_df_maker(uembs, cluster_labels, titles)
  clustered, outliers = result_splitter(result)
  trace_cluster, trace_outlier = result_tracer(clustered, outliers)
  return trace_cluster, trace_outlier

In [5]:
def subplotter(trace_nested_list: list, titles: list, base_size=1000) -> go.Figure:
    
    row_count = len(trace_nested_list)
    col_count = len(trace_nested_list[0])
    
    fig = make_subplots(
        rows=row_count, 
        cols=col_count,
        subplot_titles=(titles),
        vertical_spacing=0.02,
        horizontal_spacing=0.02
    )

    for i, row in enumerate(trace_nested_list):
        for j, col in enumerate(row):

            # adding both outlieers and clustered
            for trace in col:
                fig.add_trace(trace, row=i+1, col=i+1)
    
    # figure settings
    fig.update_xaxes(visible=False)
    fig.update_yaxes(visible=False)
    
    fig.update_layout(width=base_size*col_count, height=base_size*row_count, plot_bgcolor='rgba(250,250,250,1)')

    return fig

# Data Part

In [6]:
# got data from kaggle: https://www.kaggle.com/datasets/datasnaek/youtube-new?resource=download

df_whole = pd.read_csv("kaggle-youtube/USvideos.csv")

df = df_whole[["title"]].copy()

print(df_whole.shape)

df_whole.head(3)

(40949, 16)


video_id trending_date  \
0  2kyS6SvSYSE      17.14.11   
1  1ZAPwfrtAFY      17.14.11   
2  5qpjK5DgCt4      17.14.11   

                                                            title  \
0                              WE WANT TO TALK ABOUT OUR MARRIAGE   
1  The Trump Presidency: Last Week Tonight with John Oliver (HBO)   
2           Racist Superman | Rudy Mancuso, King Bach & Lele Pons   

     channel_title  category_id              publish_time  \
0     CaseyNeistat           22  2017-11-13T17:13:01.000Z   
1  LastWeekTonight           24  2017-11-13T07:30:00.000Z   
2     Rudy Mancuso           23  2017-11-12T19:05:24.000Z   

                                                                                                                                                                                                      tags  \
0                                                                                                                                                                                          SHANtell martin   
1                                                                                                   last week tonight trump presidency|"last week tonight donald trump"|"john oliver trump"|"donald trump"   
2  racist superman|"rudy"|"mancuso"|"king"|"bach"|"racist"|"superman"|"love"|"rudy mancuso poo bear black white official music video"|"iphone x by pineapple"|"lelepons"|"hannahstocking"|"rudymancuso"...   

     views   likes  dislikes  comment_count  \
0   748374   57527      2966          15954   
1  2418783   97185      6146          12703   
2  3191434  146033      5339           8181   

                                   thumbnail_link  comments_disabled  \
0  https://i.ytimg.com/vi/2kyS6SvSYSE/default.jpg              False   
1  https://i.ytimg.com/vi/1ZAPwfrtAFY/default.jpg              False   
2  https://i.ytimg.com/vi/5qpjK5DgCt4/default.jpg              False   

   ratings_disabled  video_error_or_removed  \
0             False                   False   
1             False                   False   
2             False                   False   

                                                                                                                                                                                               description  
0  SHANTELL'S CHANNEL - https://www.youtube.com/shantellmartin\nCANDICE - https://www.lovebilly.com\n\nfilmed this video in 4k on this -- http://amzn.to/2sTDnRZ\nwith this lens -- http://amzn.to/2rUJ...  
1  One year after the presidential election, John Oliver discusses what we've learned so far and enlists our catheter cowboy to teach Donald Trump what he hasn't.\n\nConnect with Last Week Tonight on...  
2  WATCH MY PREVIOUS VIDEO ▶ \n\nSUBSCRIBE ► https://www.youtube.com/channel/UC5jkXpfnBhlDjqh0ir5FsIQ?sub_confirmation=1\n\nTHANKS FOR WATCHING! LIKE & SUBSCRIBE FOR MORE VIDEOS!\n-------------------...

In [7]:
df["title_clean"] = df["title"].apply(string_cleaner)

df.head(5)

title  \
0                              WE WANT TO TALK ABOUT OUR MARRIAGE   
1  The Trump Presidency: Last Week Tonight with John Oliver (HBO)   
2           Racist Superman | Rudy Mancuso, King Bach & Lele Pons   
3                                Nickelback Lyrics: Real or Fake?   
4                                        I Dare You: GOING BALD!?   

                                                   title_clean  
0                           we want to talk about our marriage  
1  the trump presidency last week tonight with john oliver hbo  
2           racist superman  rudy mancuso king bach  lele pons  
3                               nickelback lyrics real or fake  
4                                        i dare you going bald

# ML Part

In [8]:
embs = model.encode(df["title_clean"])

embs.shape

(40949, 768)

In [9]:
uembs = UMAP(n_neighbors=100).fit_transform(embs)

uembs.shape

(40949, 2)

In [10]:
fig = px.scatter(x=uembs[:,0], y=uembs[:,1])

fig.update_layout(width=800, height=800)
fig.update_traces(marker=dict(size=2))

fig_show_save(fig, "umap-scatter")

In [11]:
clusters = HDBSCAN(min_cluster_size=40).fit(uembs)

print(f"""
    Number of clusters: {len(set(clusters.labels_)) - 1}
    Number of rows as outliers: {clusters.labels_.tolist().count(-1)}
""")


    Number of clusters: 276
    Number of rows as outliers: 17309



In [12]:
trace_cluster, trace_outlier = result_tracer_wrapper(uembs, clusters.labels_, df["title_clean"])


col11 = [trace_cluster, trace_outlier]

row1 = [col11]

trace_list = [row1]

fig = subplotter(trace_list, ["Topics by HDBSCAN Cluster", ])

fig_show_save(fig, "topics-by-hdbscan-clusters")